1. 열린데이터광장 > 서울시 따릉이 대여소별 대여/반납 승객수 정보   
https://data.seoul.go.kr/dataList/OA-21229/F/1/datasetView.do   
2. 열린데이터광장 > 서울특별시_따릉이대여소 마스터 정보    
https://www.data.go.kr/data/15099365/fileData.do  
3. 서울시 빅데이터 캠퍼스 > 서울시 행정동별 내국인 KT 생활이동 데이터   
https://bigdata.seoul.go.kr/data/selectSampleData.do?r_id=P213&sample_data_seq=330&tab_type=&file_id=1651221780698P6PK6ELBSNSRZGLRH94502KIH&sch_text=%EC%9D%B4%EB%8F%99&sch_order=U&currentPage=1  
4. 서울시 자전거 도로 데이터 
5. 서울시 경사 데이터  

## 지하철 데이터 제공의 지연으로, 이미 제공된 '따릉이 데이터' 활용하여 분석 예정  
### 1. 따릉이 계절별/시간대별 대여 및 반납 분석을 통해 따릉이 배치 제안 
### 2. 따릉이 대여/반납 장소 데이터를 통해 자전거 도로의 확충이 필요한 지역 분석 
### 3. 따릉이 및 유동인구 데이터 분석을 통해 퀵보드 주차장 입지 선정  

In [10]:
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt

In [48]:
location=pd.read_csv("./data/bicycle_location.csv",encoding='cp949')
bicycle=pd.read_csv("./data/tpss_bcycl_od_statnhm_20220531.csv",encoding='cp949')
walk=pd.read_csv("./data/WALK_08_29__9_4.csv",encoding='cp949')

In [12]:
location=location.iloc[:,[0,3,4]]
location['좌표']=list(zip(location['위도'].round(6),location['위도'].round(6)))
location

대여소ID         위도          경도                      좌표
0         2   0.000000    0.000000              (0.0, 0.0)
1         3  37.549561  126.905754  (37.549561, 37.549561)
2         4  37.555649  126.910629  (37.555649, 37.555649)
3         5  37.554951  126.910835  (37.554951, 37.554951)
4         6  37.550629  126.914986  (37.550629, 37.550629)
...     ...        ...         ...                     ...
3128   3140  37.556877  126.936035  (37.556877, 37.556877)
3129   3141  37.539139  127.121620  (37.539139, 37.539139)
3130   3142  37.516693  126.908073  (37.516693, 37.516693)
3131   3143  37.472202  126.933907  (37.472202, 37.472202)
3132   3144  37.482853  127.005974  (37.482853, 37.482853)

[3133 rows x 4 columns]

In [49]:
bicycle

기준_날짜  기준_시간대 시작_대여소_ID 종료_대여소_ID  전체_건수  전체_이용_분  전체_이용_거리
0       20220531      10   ST-2038   ST-2038      1        1       111
1       20220531      15     ST-17     ST-17      1        1        88
2       20220531      20    ST-827    ST-827      1        1        40
3       20220531      25   ST-2325   ST-2325      2        1        88
4       20220531      35    ST-175    ST-175      1        1        80
...          ...     ...       ...       ...    ...      ...       ...
322927  20220531    2015     ST-99     ST-99      7      304     13476
322928  20220531    2250     ST-98     ST-99      6       33      3603
322929  20220531    1805   ST-1712   ST-2045      7       22      4909
322930  20220531    1705    ST-890    ST-772      8       36      7652
322931  20220531    1710    ST-890    ST-772      9       39      8521

[322932 rows x 7 columns]

In [13]:
bicycle['시작_대여소_ID'] = bicycle['시작_대여소_ID'].str.split('-').str[1]
bicycle['종료_대여소_ID'] = bicycle['종료_대여소_ID'].str.split('-').str[1]
bicycle = bicycle.iloc[:,:4]
bicycle=bicycle[bicycle["시작_대여소_ID"]!=bicycle["종료_대여소_ID"]]

bicycle['기준_시간대']=bicycle['기준_시간대'].apply(lambda x: str(x).zfill(4))
day_time=bicycle['기준_날짜'].astype(str)+bicycle['기준_시간대']
bicycle['기준_날짜시간']=pd.to_datetime(day_time,format="%Y%m%d%H%M")
bicycle=bicycle.iloc[:,2:]

bicycle.sort_values('기준_날짜시간',inplace=True)
bicycle.reset_index(drop=True,inplace=True)

bicycle['시작_대여소_ID']=bicycle['시작_대여소_ID'].astype(int)
bicycle['종료_대여소_ID']=bicycle['종료_대여소_ID'].astype(int)

bicycle

시작_대여소_ID  종료_대여소_ID             기준_날짜시간
0            1006       2770 2022-05-31 00:00:00
1             371       2331 2022-05-31 00:00:00
2             360        189 2022-05-31 00:00:00
3             338        175 2022-05-31 00:00:00
4             330        437 2022-05-31 00:00:00
...           ...        ...                 ...
303210        645       2136 2022-05-31 23:55:00
303211        644       1105 2022-05-31 23:55:00
303212         64       2669 2022-05-31 23:55:00
303213        605       2703 2022-05-31 23:55:00
303214        646       2137 2022-05-31 23:55:00

[303215 rows x 3 columns]

In [16]:
bicycle_location=pd.merge(bicycle, location, how='left', left_on='시작_대여소_ID', right_on='대여소ID')
bicycle_location.rename(columns={'좌표':'시작_좌표'},inplace=True)
bicycle_location=pd.merge(bicycle_location, location, how='left', left_on='종료_대여소_ID', right_on='대여소ID')
bicycle_location.rename(columns={'좌표':'종료_좌표'},inplace=True)
bicycle_location=bicycle_location.iloc[:,[2,4,5,6,8,9,10]]
bicycle_location

기준_날짜시간       위도_x        경도_x                   시작_좌표  \
0      2022-05-31 00:00:00  37.536377  126.871513  (37.536377, 37.536377)   
1      2022-05-31 00:00:00  37.548290  127.062462    (37.54829, 37.54829)   
2      2022-05-31 00:00:00  37.561096  127.036797  (37.561096, 37.561096)   
3      2022-05-31 00:00:00  37.566994  127.003464  (37.566994, 37.566994)   
4      2022-05-31 00:00:00  37.530167  127.007439  (37.530167, 37.530167)   
...                    ...        ...         ...                     ...   
303210 2022-05-31 23:55:00  37.640327  127.013359  (37.640327, 37.640327)   
303211 2022-05-31 23:55:00  37.624157  127.018623  (37.624157, 37.624157)   
303212 2022-05-31 23:55:00  37.524837  126.934906  (37.524837, 37.524837)   
303213 2022-05-31 23:55:00  37.635109  127.068329  (37.635109, 37.635109)   
303214 2022-05-31 23:55:00  37.638805  127.028358  (37.638805, 37.638805)   

             위도_y        경도_y                   종료_좌표  
0       37.520916  126.840958  (37.520916, 37.520916)  
1       37.555141  127.071106  (37.555141, 37.555141)  
2       37.560474  127.014076  (37.560474, 37.560474)  
3       37.573242  127.015907  (37.573242, 37.573242)  
4       37.544895  126.969383  (37.544895, 37.544895)  
...           ...         ...                     ...  
303210  37.647934  127.014572  (37.647934, 37.647934)  
303211  37.613956  127.030251  (37.613956, 37.613956)  
303212  37.481167  126.997589  (37.481167, 37.481167)  
303213  37.632145  127.069824  (37.632145, 37.632145)  
303214  37.637970  127.025902    (37.63797, 37.63797)  

[303215 rows x 7 columns]

In [18]:
# 시작 - 도착 경로 
graph1=pd.pivot_table(bicycle_location,index=["위도_x","경도_x","위도_y","경도_y","시작_좌표","종료_좌표"],aggfunc='count')
graph1.reset_index(inplace=True)
graph1.rename(columns={'기준_날짜시간':'횟수'},inplace=True)
graph1

위도_x        경도_x       위도_y        경도_y                   시작_좌표  \
0      37.430977  127.070335  37.447659  127.055016  (37.430977, 37.430977)   
1      37.430977  127.070335  37.454357  127.062103  (37.430977, 37.430977)   
2      37.430977  127.070335  37.457226  127.059006  (37.430977, 37.430977)   
3      37.430977  127.070335  37.475605  127.050377  (37.430977, 37.430977)   
4      37.430977  127.070335  37.482979  127.042259  (37.430977, 37.430977)   
...          ...         ...        ...         ...                     ...   
88317  37.691013  127.049164  37.668671  127.047981  (37.691013, 37.691013)   
88318  37.691013  127.049164  37.674366  127.059471  (37.691013, 37.691013)   
88319  37.691013  127.049164  37.677219  127.048637  (37.691013, 37.691013)   
88320  37.691013  127.049164  37.679848  127.050385  (37.691013, 37.691013)   
88321  37.691013  127.049164  37.685234  127.049858  (37.691013, 37.691013)   

                        종료_좌표  횟수  
0      (37.447659, 37.447659)   4  
1      (37.454357, 37.454357)   2  
2      (37.457226, 37.457226)   2  
3      (37.475605, 37.475605)   2  
4      (37.482979, 37.482979)   2  
...                       ...  ..  
88317  (37.668671, 37.668671)   7  
88318  (37.674366, 37.674366)   2  
88319  (37.677219, 37.677219)   2  
88320  (37.679848, 37.679848)   8  
88321  (37.685234, 37.685234)   2  

[88322 rows x 7 columns]

In [38]:
print(graph1['횟수'].sort_values().unique())
np.percentile(graph1['횟수'].sort_values().unique(),[25,50,75],interpolation='nearest')

[ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24
 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 46 47 48 49
 50 51 52 53 54 55 56 57 58 59 60 61 63 64 65 67 68 69 71 82 86]


array([18, 35, 53])

In [41]:
graph1_25=graph1[graph1['횟수']<18]
graph1_50=graph1[(graph1['횟수']>=18) & (graph1['횟수']<35)]
graph1_75=graph1[(graph1['횟수']>=35) & (graph1['횟수']<53)]
graph1_100=graph1[graph1['횟수']>=53]

In [47]:
import folium
center = [37.541, 126.986]
mapp = folium.Map(location=center, zoom_start=11)

folium.PolyLine(
    locations = [list(zip(graph1_25['위도_x'],graph1_25['경도_x'])),list(zip(graph1_25['위도_y'],graph1_25['경도_y']))],
    opacity = 0.3 , color='red'
).add_to(mapp)
folium.PolyLine(
    locations = [list(zip(graph1_50['위도_x'],graph1_50['경도_x'])),list(zip(graph1_50['위도_y'],graph1_50['경도_y']))],
    opacity = 0.3 , color='green'
).add_to(mapp)
folium.PolyLine(
    locations = [list(zip(graph1_75['위도_x'],graph1_75['경도_x'])),list(zip(graph1_75['위도_y'],graph1_75['경도_y']))],
    opacity = 0.3 , color='blue'
).add_to(mapp)
folium.PolyLine(
    locations = [list(zip(graph1_100['위도_x'],graph1_100['경도_x'])),list(zip(graph1_100['위도_y'],graph1_100['경도_y']))],
    opacity = 0.3 , color='purple'
).add_to(mapp)
mapp